## Buy Box Datenanalyse

In [1]:
import pandas as pd
import numpy as np

df = pd.read_csv('../Grunddatein/Zwischendatein/cleaned_data.csv')
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 109215 entries, 0 to 109214
Data columns (total 22 columns):
 #   Column                Non-Null Count   Dtype  
---  ------                --------------   -----  
 0   asin                  109215 non-null  object 
 1   time                  109215 non-null  object 
 2   id                    109215 non-null  float64
 3   price                 109215 non-null  float64
 4   currency              109215 non-null  object 
 5   crawlTime             109215 non-null  object 
 6   condition             109215 non-null  object 
 7   sellerName            109215 non-null  object 
 8   sellerId              109215 non-null  object 
 9   sellerbewertung       81457 non-null   float64
 10  seller_sterne         109215 non-null  float64
 11  lieferdatum           105389 non-null  object 
 12  lieferpreis           105389 non-null  float64
 13  lieferung_durch       109215 non-null  object 
 14  ranking               109215 non-null  float64
 15  

In [2]:
print("Length of the DataFrame:", df.shape[0])
num_true = (df['buyBoxWinner'] == True).sum()
print(f"The Number of Offers winning the BuyBox is {num_true}")

Length of the DataFrame: 109215
The Number of Offers winning the BuyBox is 10394


In [4]:
buy_box_counts = df['buyBoxWinner'].value_counts()
buy_box_counts

False    98728
True     10595
Name: buyBoxWinner, dtype: int64

## Generating Lists Of Asins Where Amazon is Present as a Seller and where Not

In [3]:
amazon_asin_values = df.loc[df['sellerName'].isin(['amazon', 'Amazon Warehouse ', 'Amazon US', 'Amazon UK']), 'asin'].unique()
print(f"An so vielen Asins ist Amazon als Verkäufer eingetragen:{len(amazon_asin_values)}")

# Assuming the DataFrame is named 'df'
all_asin_values = df['asin'].unique()

# Subtract the values that exist in the 'amazon_asin_values' list
non_amazon_asin_values = set(all_asin_values) - set(amazon_asin_values)
print(f"An so vielen Asins ist Amazon nicht als Verkäufer eingetragen:{len(non_amazon_asin_values)}")
print(f"So Viele unterschiedliche Asins gibt es maximal {len(all_asin_values)}")

An so vielen Asins ist Amazon als Verkäufer eingetragen:673
An so vielen Asins ist Amazon nicht als Verkäufer eingetragen:311
So Viele unterschiedliche Asins gibt es maximal 984


## Vergleich wie Oft die Seller die BuyBox gewinnen wenn Amazon nicht dabei ist.

In [4]:
## Vergleich wie Oft die Seller die BuyBox gewinnen wenn Amazon dabei ist, nicht dabei ist.
##Wie oft Seller unter Sich gewinnen
# Get the rows where the asin is in 'non_amazon_asin_values' and the 'buyBoxWinner' column is True
df_non_amazon_buy_box_winners = df.loc[(df['asin'].isin(non_amazon_asin_values)) & (df['buyBoxWinner'] == True)]
amazon_seller_names = ['amazon', 'Amazon Warehouse', 'Amazon US', 'Amazon UK']

# Get the total count of rows where the asin is in 'non_amazon_asin_values' and the 'buyBoxWinner' column is True
total_count = len(df_non_amazon_buy_box_winners)

# Get the count of rows where the value in the 'sellerName' column is not in the 'amazon_seller_names' list
seller_count = len(df_non_amazon_buy_box_winners.loc[~df_non_amazon_buy_box_winners['sellerName'].isin(amazon_seller_names)])

# Calculate the percentage
if total_count > 0:
    percentage = (seller_count / total_count) * 100
else:
    percentage = 0

# Print the percentage
print(percentage)


100.0


## Wie oft FremdSeller die BuyBox gewinnen wenn Amazon dabei ist

In [5]:
#Wie oft Seller mit Amazon gewinnen
# Get the rows where the asin is in 'amazon_asin_values' and the 'buyBoxWinner' column is True
df_amazon_buy_box_winners = df.loc[(df['asin'].isin(amazon_asin_values)) & (df['buyBoxWinner'] == True)]

# Get the total count of rows where the asin is in 'amazon_asin_values' and the 'buyBoxWinner' column is True
total_count = len(df_amazon_buy_box_winners)
print(f"The Number of BuyBoxWinning Rows for products where Amazon as a seller is present {total_count}")

# Get the count of rows where the value in the 'sellerName' column is not 'amazon' or 'Amazon Warehouse'
offer_without_amazon = df_amazon_buy_box_winners.loc[(df_amazon_buy_box_winners['sellerName'] != 'amazon') & (df_amazon_buy_box_winners['sellerName'] != 'Amazon Warehouse')]
#print(offer_without_amazon)
seller_count = len(offer_without_amazon)
print(f"The Number of BuyBoxWinning Rows where Amazon is not the winner is {seller_count}")

offer_without_amazon = df_amazon_buy_box_winners.loc[(df_amazon_buy_box_winners['sellerName'] == 'amazon') | (df_amazon_buy_box_winners['sellerName'] == 'Amazon Warehouse')]
print(f"The Number of BuyBoxWinning Rows where Amazon is the winner is {len(offer_without_amazon)}")
# Calculate the percentage
if total_count > 0:
    percentage = (seller_count / total_count) * 100
else:
    percentage = 0

# Print the percentage
print(percentage)


The Number of BuyBoxWinning Rows for products where Amazon as a seller is present 7621
The Number of BuyBoxWinning Rows where Amazon is not the winner is 1573
The Number of BuyBoxWinning Rows where Amazon is the winner is 6048
20.64033591392206


## Wie oft ist der niedrigste Preis auch der Gewinner?

In [7]:
# Group the DataFrame by 'asin' and time slot (hour)
selected_rows = df[df['condition'].isin(['Neu', 'New'])]
grouped_df = selected_rows.groupby(['asin', pd.Grouper(key='time', freq='H')])

# Define a custom function to calculate the percentage of times the cheapest price is the buyBoxWinner
def cheapest_is_buy_box_winner(group):
    # Get the row with the cheapest price
    cheapest_row = group.loc[group['price'] == group['price'].min()]
    # Check if the buyBoxWinner is True for the cheapest price row
    cheapest_bb_winner = cheapest_row.iloc[0]['buyBoxWinner']
    # Calculate the percentage
    if cheapest_bb_winner:
        return 1
    else:
        return 0

# Apply the custom function to each group
percentages = grouped_df.apply(cheapest_is_buy_box_winner)

# Calculate the overall percentage
overall_percentage = percentages.mean() * 100

# Print the overall percentage with a descriptive message
print(f"Overall percentage of times the cheapest price wins the Buy Box: {overall_percentage:.2f}%")

Overall percentage of times the cheapest price wins the Buy Box: 64.00%


## Wie oft ist der niedrigste Preis nicht der Gewinner?

In [8]:
# Convert the 'timestamp' column to a DatetimeIndex
df["time"] = pd.to_datetime(df["time"], format="%Y-%m-%d %H:%M:%S")
# Group the DataFrame by 'asin' and time slot (hour)
#Only use New Offers, cause used objects arent obligated to win the buyBox
selected_rows = df[df['condition'].isin(['Neu', 'New'])]
grouped_df = selected_rows.groupby(['asin', pd.Grouper(key='time', freq='H')])

# Define a custom function to calculate the percentage of times the cheapest price is not the buyBoxWinner
def cheapest_not_buy_box_winner(group):
    # Get the row with the cheapest price
    cheapest_row = group.loc[group['price'] == group['price'].min()]
    #print(cheapest_row[['asin', 'price', 'time','buyBoxWinner']])
    most_expensive_row = group.loc[group['price'] == group['price'].max()]
    #print(most_expensive_row[['asin', 'price', 'time','buyBoxWinner']])
    #print("--------------------------------------------")

    # Check if the buyBoxWinner is True for the cheapest price row
    cheapest_bb_winner = cheapest_row.iloc[0]['buyBoxWinner']
    # Calculate the percentage
    if not cheapest_bb_winner:
        return 1
    else:
        return 0

# Apply the custom function to each group
percentages = grouped_df.apply(cheapest_not_buy_box_winner)

# Calculate the overall percentage
overall_percentage = percentages.mean() * 100

# Print the overall percentage
print(f"Overall percentage of times the cheapest price wins the Buy Box: {overall_percentage:.2f}%")

36.00035839082519


In [9]:
df = pd.read_csv('cleaned_data.csv')

## Exclude Not New Offers and Reactive Offers

In [10]:
## Exclude all Rows where condition isnt New and which where a reactive Crawl
df = df[df['trigByReactive'] != True]
df = df[df['condition'].isin(['Neu', 'New'])]

# Wie hoch ist der Unterschied zwischen Maximalen Offerpreis und Minimalen Offerpreis. Absolut

In [12]:
### Wie hoch ist der Unterschied zwischen Maximalen Offerpreis und BuyBoxPreis. Absolut, Prozentual, Median, Durchschnitt
# Group the DataFrame by 'asin' and time slot (hour)
# Only use New Offers, because used objects are not obligated to win the buyBox
selected_rows = df[df['condition'].isin(['Neu', 'New'])]
grouped_df = selected_rows.groupby(['asin', pd.Grouper(key='time', freq='H')])

# Define a custom function to calculate the difference between the highest and cheapest price
def difference_between_highest_and_cheapest(group):
    # Get the row with the cheapest price
    cheapest_row = group.loc[group['price'] == group['price'].min()]
    # Get the row with the highest price
    highest_row = group.loc[group['price'] == group['price'].max()]
    # Calculate the difference between the highest price and the cheapest price
    difference = highest_row.iloc[0]['price'] - cheapest_row.iloc[0]['price']
    # Return the difference as a single value
    #print("--------------------------------------------")
    #print(cheapest_row[['asin', 'price', 'time','buyBoxWinner']])
    #print(highest_row[['asin', 'price', 'time','buyBoxWinner']])
    #print(difference)
    #print("--------------------------------------------")
    return difference

# Apply the custom function to each group
results = grouped_df.apply(difference_between_highest_and_cheapest)

# Find the row/asin with the highest difference
highest_difference = results.max()
highest_difference_row = results.idxmax()

# Print the results
#print("Highest Difference:", highest_difference)
#print("Highest Difference Row/Asin:", highest_difference_row)


--------------------------------------------
         asin  price                time  buyBoxWinner
1  B00000JD6K   86.9 2023-03-22 16:00:00         False
         asin  price                time  buyBoxWinner
0  B00000JD6K   95.8 2023-03-22 16:00:00          True
8.899999999999991
--------------------------------------------
--------------------------------------------
              asin  price                time  buyBoxWinner
200001  B00000JD6K   86.9 2023-03-22 17:00:00         False
              asin  price                time  buyBoxWinner
200000  B00000JD6K   95.8 2023-03-22 17:00:00          True
8.899999999999991
--------------------------------------------
--------------------------------------------
         asin  price                time  buyBoxWinner
3  B00000JD6K   86.9 2023-03-22 18:00:00         False
         asin  price                time  buyBoxWinner
2  B00000JD6K   95.8 2023-03-22 18:00:00          True
8.899999999999991
-----------------------------------------

            asin  price                time  buyBoxWinner
4840  B0009V6N1U  120.1 2023-03-23 07:00:00         False
67.31
--------------------------------------------
--------------------------------------------
            asin  price                time  buyBoxWinner
4845  B0009V6N1U  52.79 2023-03-23 08:00:00         False
            asin  price                time  buyBoxWinner
4871  B0009V6N1U  120.1 2023-03-23 08:00:00         False
67.31
--------------------------------------------
--------------------------------------------
            asin  price                time  buyBoxWinner
4876  B0009V6N1U  52.79 2023-03-23 09:00:00         False
            asin  price                time  buyBoxWinner
4902  B0009V6N1U  120.1 2023-03-23 09:00:00         False
67.31
--------------------------------------------
--------------------------------------------
            asin  price                time  buyBoxWinner
4907  B0009V6N1U  52.79 2023-03-23 10:00:00         False
            asin

--------------------------------------------
            asin  price                time  buyBoxWinner
6707  B000EENFIG  36.56 2023-03-22 18:00:00          True
            asin  price                time  buyBoxWinner
6709  B000EENFIG  45.28 2023-03-22 18:00:00         False
8.719999999999999
--------------------------------------------
--------------------------------------------
            asin  price                time  buyBoxWinner
6710  B000EENFIG  36.56 2023-03-22 19:00:00          True
            asin  price                time  buyBoxWinner
6712  B000EENFIG  45.28 2023-03-22 19:00:00         False
8.719999999999999
--------------------------------------------
--------------------------------------------
            asin  price                time  buyBoxWinner
6713  B000EENFIG  36.56 2023-03-22 20:00:00          True
            asin  price                time  buyBoxWinner
6715  B000EENFIG  45.28 2023-03-22 20:00:00         False
8.719999999999999
-------------------------

--------------------------------------------
            asin  price                time  buyBoxWinner
9006  B000SIR14M  244.2 2023-03-23 15:00:00         False
            asin   price                time  buyBoxWinner
9013  B000SIR14M  349.96 2023-03-23 15:00:00         False
105.75999999999999
--------------------------------------------
--------------------------------------------
            asin  price                time  buyBoxWinner
9015  B000SIR14M  244.2 2023-03-23 16:00:00         False
            asin   price                time  buyBoxWinner
9022  B000SIR14M  349.96 2023-03-23 16:00:00         False
105.75999999999999
--------------------------------------------
--------------------------------------------
            asin   price                time  buyBoxWinner
9027  B000T10P6O  156.55 2023-03-22 16:00:00         False
            asin   price                time  buyBoxWinner
9030  B000T10P6O  229.92 2023-03-22 16:00:00         False
73.36999999999998
---------------

            asin   price                time  buyBoxWinner
9722  B000WZ7FT2  101.43 2023-03-23 09:00:00         False
            asin   price                time  buyBoxWinner
9721  B000WZ7FT2  126.35 2023-03-23 09:00:00          True
24.919999999999987
--------------------------------------------
--------------------------------------------
            asin   price                time  buyBoxWinner
9724  B000WZ7FT2  101.43 2023-03-23 10:00:00         False
            asin   price                time  buyBoxWinner
9723  B000WZ7FT2  126.35 2023-03-23 10:00:00          True
24.919999999999987
--------------------------------------------
--------------------------------------------
            asin   price                time  buyBoxWinner
9726  B000WZ7FT2  101.43 2023-03-23 11:00:00         False
            asin  price                time  buyBoxWinner
9725  B000WZ7FT2  125.3 2023-03-23 11:00:00          True
23.86999999999999
--------------------------------------------
-------------

...

              asin   price                time  buyBoxWinner
193461  B09ZJBPQTZ  179.97 2023-03-23 05:00:00          True
0.0
--------------------------------------------
--------------------------------------------
              asin   price                time  buyBoxWinner
193463  B09ZJBPQTZ  179.96 2023-03-23 06:00:00         False
              asin   price                time  buyBoxWinner
193462  B09ZJBPQTZ  179.97 2023-03-23 06:00:00          True
193464  B09ZJBPQTZ  179.97 2023-03-23 06:00:00         False
0.009999999999990905
--------------------------------------------
--------------------------------------------
              asin   price                time  buyBoxWinner
193465  B09ZJBPQTZ  179.97 2023-03-23 07:00:00          True
              asin   price                time  buyBoxWinner
193465  B09ZJBPQTZ  179.97 2023-03-23 07:00:00          True
0.0
--------------------------------------------
--------------------------------------------
              asin   price    

--------------------------------------------
              asin   price                time  buyBoxWinner
194527  B0B59W6Z5D  775.46 2023-03-23 08:00:00         False
              asin   price                time  buyBoxWinner
194528  B0B59W6Z5D  785.54 2023-03-23 08:00:00         False
10.079999999999927
--------------------------------------------
--------------------------------------------
              asin   price                time  buyBoxWinner
194538  B0B59W6Z5D  775.46 2023-03-23 09:00:00         False
              asin   price                time  buyBoxWinner
194539  B0B59W6Z5D  785.54 2023-03-23 09:00:00         False
10.079999999999927
--------------------------------------------
--------------------------------------------
              asin   price                time  buyBoxWinner
194549  B0B59W6Z5D  775.46 2023-03-23 10:00:00         False
              asin   price                time  buyBoxWinner
194550  B0B59W6Z5D  785.54 2023-03-23 10:00:00         False
10.07

--------------------------------------------
              asin   price                time  buyBoxWinner
197043  B0BD8ZZLYC  583.86 2023-03-23 16:00:00          True
              asin   price                time  buyBoxWinner
197043  B0BD8ZZLYC  583.86 2023-03-23 16:00:00          True
0.0
--------------------------------------------
--------------------------------------------
              asin  price                time  buyBoxWinner
197052  B0BDJJY92W  489.0 2023-03-22 16:00:00          True
              asin   price                time  buyBoxWinner
197062  B0BDJJY92W  581.92 2023-03-22 16:00:00         False
92.91999999999996
--------------------------------------------
--------------------------------------------
              asin  price                time  buyBoxWinner
209069  B0BDJJY92W  489.0 2023-03-22 17:00:00          True
              asin   price                time  buyBoxWinner
209079  B0BDJJY92W  581.92 2023-03-22 17:00:00         False
92.91999999999996
-------

--------------------------------------------
              asin  price       time  buyBoxWinner
198815  B0BKQYYMLH  98.72 2023-03-23          True
198816  B0BKQYYMLH  98.72 2023-03-23         False
              asin  price       time  buyBoxWinner
198815  B0BKQYYMLH  98.72 2023-03-23          True
198816  B0BKQYYMLH  98.72 2023-03-23         False
0.0
--------------------------------------------
--------------------------------------------
              asin  price                time  buyBoxWinner
198817  B0BKQYYMLH  98.72 2023-03-23 01:00:00          True
198818  B0BKQYYMLH  98.72 2023-03-23 01:00:00         False
              asin  price                time  buyBoxWinner
198817  B0BKQYYMLH  98.72 2023-03-23 01:00:00          True
198818  B0BKQYYMLH  98.72 2023-03-23 01:00:00         False
0.0
--------------------------------------------
--------------------------------------------
              asin  price                time  buyBoxWinner
198819  B0BKQYYMLH  98.72 2023-03-23 02:0

--------------------------------------------
              asin   price                time  buyBoxWinner
199710  B0BLN6G66C  130.08 2023-03-23 06:00:00          True
              asin  price                time  buyBoxWinner
199711  B0BLN6G66C  141.9 2023-03-23 06:00:00         False
11.819999999999993
--------------------------------------------
--------------------------------------------
              asin   price                time  buyBoxWinner
199713  B0BLN6G66C  130.08 2023-03-23 07:00:00          True
              asin  price                time  buyBoxWinner
199714  B0BLN6G66C  141.9 2023-03-23 07:00:00         False
11.819999999999993
--------------------------------------------
--------------------------------------------
              asin   price                time  buyBoxWinner
199716  B0BLN6G66C  130.08 2023-03-23 08:00:00          True
              asin  price                time  buyBoxWinner
199717  B0BLN6G66C  141.9 2023-03-23 08:00:00         False
11.81999999

In [13]:
# Print the results
print("Highest Difference:", highest_difference)
print("Highest Difference Row/Asin:", highest_difference_row)

Highest Difference: 772.78
Highest Difference Row/Asin: ('B07KSBWFZS', Timestamp('2023-03-22 16:00:00', freq='H'))


# Prozentualer Unterschied zwischen minimalen und maximalen Preis über alle Produkte hinweg

In [16]:
# Convert the 'time' column to a DatetimeIndex
df['time'] = pd.to_datetime(df['time'], format='%Y-%m-%d-%H')

# Group the DataFrame by 'asin' and time slot (hour)
selected_rows = df[df['condition'].isin(['Neu', 'New'])]
grouped_df = selected_rows.groupby(['asin', pd.Grouper(key='time', freq='H')])

# Define a custom function to calculate the average percentage difference between the Price of the buyBoxWinning Row and the most expensive row
def avg_price_diff(group):
    # Get the row with the highest price
    highest_price_row = group.loc[group['price'] == group['price'].max()]
    highest_price = highest_price_row.iloc[0]['price']
    
    # Get the row with the buyBox winning offer
    buyBox_winner_row = group.loc[group['buyBoxWinner'] == True]
    
    # Check if there is a buyBox winner for the group
    if buyBox_winner_row.empty:
        return None
    
    # Get the price of the buyBox winning offer
    buyBox_winner_price = buyBox_winner_row.iloc[0]['price']
    
    # Calculate the percentage difference between the highest price and the buyBox winning price
    diff_percent = ((highest_price - buyBox_winner_price) / highest_price) * 100
    
    # Return the percentage difference
    return diff_percent

# Apply the custom function to each group
price_diffs = grouped_df.apply(avg_price_diff)

# Drop the groups where there is no buyBox winner
price_diffs = price_diffs.dropna()

# Calculate the overall average percentage difference
overall_avg_diff = price_diffs.mean()

# Print the overall average percentage difference
print(f"Overall average percentage difference between the highest price and the Buy Box-winning price: {overall_avg_diff:.2f}%")

Overall average percentage difference between the highest price and the Buy Box-winning price: 23.07%


# Prozentualer Unterschied zwischen BuyBoxPreis und maximalen Preis über alle Produkte hinweg

In [17]:
# Group the DataFrame by 'asin' and time slot (hour)
selected_rows = df[df['condition'].isin(['Neu', 'New'])]
grouped_df = selected_rows.groupby(['asin', pd.Grouper(key='time', freq='H')])

# Define a custom function to calculate the average percentage difference between the Price of the buyBoxWinning Row and the most expensive row
def avg_price_diff(group):
    # Get the row with the highest price
    highest_price_row = group.loc[group['price'] == group['price'].max()]
    highest_price = highest_price_row.iloc[0]['price']
    
    # Get the row with the cheapest price
    cheapest_row = group.loc[group['price'] == group['price'].min()]
    cheapest_price = cheapest_row.iloc[0]['price']
    
    # Check if the buyBoxWinner is True for the cheapest price row
    cheapest_bb_winner = cheapest_row.iloc[0]['buyBoxWinner']
    
    # Calculate the percentage difference
    if cheapest_bb_winner:
        diff_percent = ((highest_price - cheapest_price) / highest_price) * 100
        return diff_percent
    else:
        return None

# Apply the custom function to each group
price_diffs = grouped_df.apply(avg_price_diff)

# Calculate the overall average percentage difference
overall_avg_diff = price_diffs.mean()

# Print the overall average percentage difference
print(f"Overall average percentage difference between the price of the Buy Box-winning row and the most expensive row: {overall_avg_diff:.2f}%")



Overall average percentage difference between the price of the Buy Box-winning row and the most expensive row: 23.92%


# Wie hoch ist der Unterschied zwischen Maximalen Offerpreis und BuyBoxWinning Preis. Absolut und Prozentual

In [18]:
# Convert the 'time' column to a DatetimeIndex
df['time'] = pd.to_datetime(df['time'], format='%Y-%m-%d-%H')

# Group the DataFrame by 'asin' and time slot (hour)
# Only use New Offers, because used objects are not obligated to win the buyBox
selected_rows = df[df['condition'].isin(['Neu', 'New'])]
grouped_df = selected_rows.groupby(['asin', pd.Grouper(key='time', freq='H')])

# Define a custom function to calculate the difference between the highest and buyBox winning price
def difference_between_highest_and_buyBoxWinner(group):
    # Get the row with the buyBox winning offer
    buyBox_winner_row = group.loc[group['buyBoxWinner'] == True]
    # Check if there is a buyBox winner for the group
    if buyBox_winner_row.empty:
        return None
    # Get the row with the highest price
    highest_price_row = group.loc[group['price'] == group['price'].max()]
    # Calculate the difference between the highest price and the buyBox winning price
    difference = highest_price_row.iloc[0]['price'] - buyBox_winner_row.iloc[0]['price']
    # Return the difference as a single value
    #print("--------------------------------------------")
    #print(buyBox_winner_row[['asin', 'price', 'time', 'buyBoxWinner']])
    #print(highest_price_row[['asin', 'price', 'time', 'buyBoxWinner']])
    #print(difference)
    #print("--------------------------------------------")
    return difference

# Apply the custom function to each group
results = grouped_df.apply(difference_between_highest_and_buyBoxWinner)

# Drop the groups where there is no buyBox winner
results = results.dropna()

# Find the row/asin with the highest difference
highest_difference = results.max()
highest_difference_row = results.idxmax()

# Print the results
#print("Highest Difference:", highest_difference)
#print("Highest Difference Row/Asin:", highest_difference_row)


In [19]:
# Print the results
print("Highest Difference:", highest_difference)
print("Highest Difference Row/Asin:", highest_difference_row)

Highest Difference: 772.78
Highest Difference Row/Asin: ('B07KSBWFZS', Timestamp('2023-03-22 16:00:00', freq='H'))


# Wie lange hält ein Verkäufer die BuyBox im Schnitt

In [20]:
# Group the dataframe by 'asin' and sort the rows within each group by the 'time' column
df_grouped = df.groupby('asin', group_keys=False).apply(lambda x: x.sort_values('time'))

# If you want to reset the index of the resulting dataframe, you can use the reset_index method
df_grouped = df_grouped.reset_index(drop=True)

# Print the sorted dataframe
df_grouped.head()


asin                time        id  price currency  \
0  B00000JD6K 2023-03-22 16:00:00  343568.0   95.8        €   
1  B00000JD6K 2023-03-22 16:00:00  344038.0   86.9        €   
2  B00000JD6K 2023-03-22 17:00:00  343568.0   95.8        €   
3  B00000JD6K 2023-03-22 17:00:00  344038.0   86.9        €   
4  B00000JD6K 2023-03-22 18:00:00  353250.0   86.9        €   

                    crawlTime condition                 sellerName  \
0  2023-03-22 16:55:20.125842       Neu                      Kidia   
1  2023-03-22 16:55:20.315580       Neu  STILE IMMAGINE DIGITAL HD   
2  2023-03-22 16:55:20.125842       Neu                      Kidia   
3  2023-03-22 16:55:20.315580       Neu  STILE IMMAGINE DIGITAL HD   
4  2023-03-22 18:00:23.106664       Neu  STILE IMMAGINE DIGITAL HD   

         sellerId  sellerbewertung  ...  lieferpreis  \
0  A2XUKJNGI8V9XU            46.56  ...          0.0   
1  A16E8RFMSALSSB            28.13  ...          9.9   
2  A2XUKJNGI8V9XU            46.56  ...          0.0   
3  A16E8RFMSALSSB            28.13  ...          9.9   
4  A16E8RFMSALSSB            28.13  ...          9.9   

             lieferung_durch  ranking buyBoxWinner  numberOfSellers  \
0                     Amazon      0.0         True              2.0   
1  STILE IMMAGINE DIGITAL HD      1.0        False              1.0   
2                     Amazon      0.0         True              2.0   
3  STILE IMMAGINE DIGITAL HD      1.0        False              1.0   
4  STILE IMMAGINE DIGITAL HD      1.0        False              1.0   

   trigByReactive  time_gap  copyed_cause_missing  Fulfillment_type  date_diff  
0           False       0.0                 False               FBA        3.0  
1           False       0.0                 False               FBM       27.0  
2           False      -1.0                  True               FBA        3.0  
3           False      -1.0                  True               FBM       27.0  
4           False       0.0                 False               FBM       27.0  

[5 rows x 22 columns]

In [21]:
# Filter the rows where 'buyBoxWinner' is True
winning_rows = df[df['buyBoxWinner']]

# Sort the winning rows by 'asin' and 'time'
winning_rows = winning_rows.sort_values(['asin', 'time'])

# Calculate the time difference between consecutive winning rows for each ASIN
winning_rows['time_diff'] = winning_rows.groupby('asin')['time'].diff()

# Only include time differences greater than 0
winning_rows = winning_rows[winning_rows['time_diff'].dt.total_seconds() > 0]

# Aggregate the time differences by ASIN and by 'sellerName'
time_agg = winning_rows.groupby(['asin', 'sellerName'])['time_diff'].sum().reset_index()

# Calculate the average winning time across all sellers who win the BuyBox
average_winning_time = time_agg['time_diff'].mean()

# Calculate the minimum, and maximum winning time across all groups
min_winning_time = time_agg['time_diff'].min()
max_winning_time = time_agg['time_diff'].max()

# Find the seller with the longest BuyBox holding time
longest_buybox_holder = time_agg.loc[time_agg['time_diff'].idxmax(), 'sellerName']

# Filter sellers with winning time longer than 9 hours
sellers_longer_than_9_hours = time_agg[time_agg['time_diff'] > pd.Timedelta(hours=4)]

print("Average winning time:", average_winning_time)
print("Minimum winning time:", min_winning_time)
print("Maximum winning time:", max_winning_time)
print("Seller holding the BuyBox the longest:", longest_buybox_holder)

print("\nSellers with winning time longer than 9 hours:")
for index, row in sellers_longer_than_9_hours.iterrows():
    print(f"ASIN: {row['asin']}, Seller: {row['sellerName']}, Winning Time: {row['time_diff']}")


Average winning time: 0 days 17:54:06.005267778
Minimum winning time: 0 days 01:00:00
Maximum winning time: 1 days 00:00:00
Seller holding the BuyBox the longest: amazon

Sellers with winning time longer than 9 hours:
ASIN: B00000JD6K, Seller: Kidia, Winning Time: 0 days 23:00:00
ASIN: B00005KIRS, Seller: amazon, Winning Time: 1 days 00:00:00
ASIN: B00008K61M, Seller: amazon, Winning Time: 1 days 00:00:00
ASIN: B00008K61N, Seller: amazon, Winning Time: 1 days 00:00:00
ASIN: B0000C72GD, Seller: STILE IMMAGINE DIGITAL HD, Winning Time: 1 days 00:00:00
ASIN: B0000D85OD, Seller: amazon, Winning Time: 1 days 00:00:00
ASIN: B0000WOK04, Seller: amazon, Winning Time: 1 days 00:00:00
ASIN: B0000WOK9A, Seller: BWBahn, Winning Time: 1 days 00:00:00
ASIN: B0001GRVJQ, Seller: amazon, Winning Time: 1 days 00:00:00
ASIN: B00022749Q, Seller: amazon, Winning Time: 1 days 00:00:00
ASIN: B0002CZU1U, Seller: Musikhaus Kirstein GmbH, Winning Time: 1 days 00:00:00
ASIN: B0002CZYW0, Seller: HeBa - Sound & Mu

## Price changes while winning the BuyBox?

In [22]:
# 1. Filter out the rows where buyBoxWinner is True
winning_rows = df[df['buyBoxWinner']]

# 2. Group the data by asin and sellerName
grouped = winning_rows.groupby(['asin', 'sellerName'])

# 3. Calculate the number of price changes for each group
price_changes = grouped['price'].apply(lambda x: x.ne(x.shift()).sum()).reset_index(name='price_change_count')

# Merge price_changes back to the winning_rows dataframe
winning_rows = winning_rows.merge(price_changes, on=['asin', 'sellerName'])

# 4. Calculate the average and maximum number of price changes
avg_price_changes = winning_rows['price_change_count'].mean()
max_price_changes = winning_rows['price_change_count'].max()

print(f"Average price changes: {avg_price_changes}")
print(f"Maximum price changes: {max_price_changes}")

# 5. Calculate the average percent difference in price changes
winning_rows['price_pct_change'] = winning_rows.groupby(['asin', 'sellerName'])['price'].pct_change()
avg_pct_diff = winning_rows['price_pct_change'].mean() * 100

print(f"Average percent difference in price changes: {avg_pct_diff}%")

# 6. Find the seller with the most price changes and print their rows
max_changes_seller = winning_rows.loc[winning_rows['price_change_count'] == max_price_changes]
max_seller_name = max_changes_seller['sellerName'].iloc[0]
max_seller_asin = max_changes_seller['asin'].iloc[0]

print(f"Seller with most price changes: {max_seller_name}, ASIN: {max_seller_asin}")

max_seller_rows = winning_rows[(winning_rows['sellerName'] == max_seller_name) & (winning_rows['asin'] == max_seller_asin)]
print("Rows where the seller with the most price changes updates their price:")
max_seller_rows




Average price changes: 5.072005064092419
Maximum price changes: 22
Average percent difference in price changes: 0.012098399582035662%
Seller with most price changes: MusicScout, ASIN: B08KJNYWX8
Rows where the seller with the most price changes updates their price:


asin                time        id   price currency  \
13599  B08KJNYWX8 2023-03-22 16:00:00  341770.0  250.28        €   
13600  B08KJNYWX8 2023-03-22 17:00:00  350975.0  250.26        €   
13601  B08KJNYWX8 2023-03-22 19:00:00  360177.0  250.24        €   
13602  B08KJNYWX8 2023-03-22 20:00:00  369469.0  250.20        €   
13603  B08KJNYWX8 2023-03-22 21:00:00  378680.0  250.18        €   
13604  B08KJNYWX8 2023-03-22 22:00:00  387932.0  250.14        €   
13605  B08KJNYWX8 2023-03-22 23:00:00  397200.0  250.08        €   
13606  B08KJNYWX8 2023-03-23 00:00:00  406460.0  250.03        €   
13607  B08KJNYWX8 2023-03-23 01:00:00  414967.0  250.00        €   
13608  B08KJNYWX8 2023-03-23 02:00:00  423942.0  249.95        €   
13609  B08KJNYWX8 2023-03-23 04:00:00  432458.0  247.86        €   
13610  B08KJNYWX8 2023-03-23 05:00:00  441784.0  249.94        €   
13611  B08KJNYWX8 2023-03-23 06:00:00  451088.0  249.90        €   
13612  B08KJNYWX8 2023-03-23 07:00:00  460516.0  249.88        €   
13613  B08KJNYWX8 2023-03-23 08:00:00  469857.0  249.86        €   
13614  B08KJNYWX8 2023-03-23 09:00:00  479106.0  249.83        €   
13615  B08KJNYWX8 2023-03-23 10:00:00  488319.0  249.80        €   
13616  B08KJNYWX8 2023-03-23 11:00:00  497537.0  249.78        €   
13617  B08KJNYWX8 2023-03-23 12:00:00  506840.0  247.68        €   
13618  B08KJNYWX8 2023-03-23 13:00:00  516103.0  249.76        €   
13619  B08KJNYWX8 2023-03-23 15:00:00  525320.0  249.76        €   
13620  B08KJNYWX8 2023-03-23 16:00:00  534603.0  249.71        €   
13621  B08KJNYWX8 2023-03-22 18:00:00  350975.0  250.26        €   

                        crawlTime condition  sellerName       sellerId  \
13599  2023-03-22 16:54:19.573924       Neu  MusicScout  AHTOZAEWYWWP3   
13600  2023-03-22 17:59:25.616300       Neu  MusicScout  AHTOZAEWYWWP3   
13601  2023-03-22 19:04:32.048797       Neu  MusicScout  AHTOZAEWYWWP3   
13602  2023-03-22 20:10:14.123591       Neu  MusicScout  AHTOZAEWYWWP3   
13603  2023-03-22 21:16:15.343357       Neu  MusicScout  AHTOZAEWYWWP3   
13604  2023-03-22 22:21:48.519934       Neu  MusicScout  AHTOZAEWYWWP3   
13605  2023-03-22 23:27:13.082547       Neu  MusicScout  AHTOZAEWYWWP3   
13606  2023-03-23 00:33:33.554383       Neu  MusicScout  AHTOZAEWYWWP3   
13607  2023-03-23 01:46:32.817455       Neu  MusicScout  AHTOZAEWYWWP3   
13608  2023-03-23 02:57:20.359477       Neu  MusicScout  AHTOZAEWYWWP3   
13609  2023-03-23 04:06:06.833942       Neu  MusicScout  AHTOZAEWYWWP3   
13610  2023-03-23 05:11:25.448091       Neu  MusicScout  AHTOZAEWYWWP3   
13611  2023-03-23 06:17:15.851052       Neu  MusicScout  AHTOZAEWYWWP3   
13612  2023-03-23 07:22:28.505168       Neu  MusicScout  AHTOZAEWYWWP3   
13613  2023-03-23 08:27:43.687732       Neu  MusicScout  AHTOZAEWYWWP3   
13614  2023-03-23 09:33:01.952896       Neu  MusicScout  AHTOZAEWYWWP3   
13615  2023-03-23 10:37:59.781203       Neu  MusicScout  AHTOZAEWYWWP3   
13616  2023-03-23 11:44:09.941900       Neu  MusicScout  AHTOZAEWYWWP3   
13617  2023-03-23 12:50:46.162478       Neu  MusicScout  AHTOZAEWYWWP3   
13618  2023-03-23 13:57:08.673757       Neu  MusicScout  AHTOZAEWYWWP3   
13619  2023-03-23 15:02:16.479266       Neu  MusicScout  AHTOZAEWYWWP3   
13620  2023-03-23 16:07:24.485297       Neu  MusicScout  AHTOZAEWYWWP3   
13621  2023-03-22 17:59:25.616300       Neu  MusicScout  AHTOZAEWYWWP3   

       sellerbewertung  ...  ranking buyBoxWinner  numberOfSellers  \
13599         32094.80  ...      0.0         True              3.0   
13600         32094.80  ...      0.0         True              3.0   
13601         32095.75  ...      0.0         True              3.0   
13602         32095.75  ...      0.0         True              3.0   
13603         32095.75  ...      0.0         True              3.0   
13604         32095.75  ...      0.0         True              3.0   
13605         32095.75  ...      0.0         True              3.0   
13606         32095.75  ...      0.0       

In [23]:
max_seller_rows.to_csv('../Grunddatein/Zwischendatein/SellerWithMostPriceChanges.csv', index=False)